First we make sure that the IgniteUI Web Components environment is loaded.

In [1]:
from IPython.display import Javascript, HTML

HTML("""
<script type="importmap-shim">
{
  "imports": {
    "igniteui-webcomponents-charts": "https://unpkg.com/igniteui-webcomponents-charts@1.2.1/fesm2015/igniteui-webcomponents-charts.js",
    "igniteui-webcomponents-grids": "https://unpkg.com/igniteui-webcomponents-grids@1.2.1/fesm2015/igniteui-webcomponents-grids.js",
     "igniteui-webcomponents-layouts": "https://unpkg.com/igniteui-webcomponents-layouts@1.2.1/fesm2015/igniteui-webcomponents-layouts.js",
      "igniteui-webcomponents-inputs": "https://unpkg.com/igniteui-webcomponents-inputs@1.2.1/fesm2015/igniteui-webcomponents-inputs.js",
    "igniteui-webcomponents-core": "https://unpkg.com/igniteui-webcomponents-core@1.2.1/fesm2015/igniteui-webcomponents-core.js",
    "lit-html": "https://unpkg.com/lit-html@1.3.0/lit-html.js"
  }
}
</script>
<script type="module-shim">
import * as igCore from 'igniteui-webcomponents-core';
import * as igCharts from 'igniteui-webcomponents-charts';
import * as igGrids from 'igniteui-webcomponents-grids';

if (!window.igCore) {
  window.igCore = igCore;
  window.igCharts = igCharts;
  igCore.ModuleManager.register(
  igCharts.IgcCategoryChartModule,
  igCharts.IgcLegendModule,
  igGrids.IgcDataGridModule);
}
</script>
<script src="https://unpkg.com/es-module-shims@0.9.0/dist/es-module-shims.js"></script>
""")

Next we create a helper method that aids in creating charts.

In [2]:
%%javascript
window.displayChart = function(data, element, options) {
    data = JSON.parse(data);
    if (options["extractTitle"]) {
        for (var i = 0; i < data.length; i++) {
            if (data[i].length > 0) {
                data[i].title = data[i][0][options["extractTitle"]];            
            }
        }
        
    }
    var chart = document.createElement("igc-category-chart");
    chart.style.margin = "30px";
    chart.width = "450px";
    chart.height = "300px";
    for (var p in options) {
        chart[p] = options[p];
    }
    chart.dataSource = data;
    
    element.appendChild(chart);
}

<IPython.core.display.Javascript object>

Next we create a helper method that aids in creating grids.

In [3]:
%%javascript
window.displayGrid = function(data, element, options) {
    var flattened = [];
    data = JSON.parse(data);
    if (data.length > 0 && data[0].length > 0) {
        for (var i = 0; i < data.length; i++) {
            for (var j = 0; j < data[i].length; j++) {
                flattened.push(data[i][j]);
            }
        }
    }

    var grid = document.createElement("igc-data-grid");
    grid.width = "450px";
    grid.height = "300px";
    
    for (var p in options) {
        grid[p] = options[p];
    }
    grid.dataSource = flattened;
    
    element.appendChild(grid);
}

<IPython.core.display.Javascript object>

Next we download and process this [Covid Data](https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-states.csv) and display the deaths by state.

In [4]:
import json
import pandas as pd
from IPython.display import Javascript

c = pd.read_csv("https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-states.csv");
c = c[(c.state != 'District of Columbia') & (c.state != 'Virgin Islands') & (c.state != 'Guam') & (c.state != 'Northern Mariana Islands') & (c.state != 'Puerto Rico')]
states = [pd.DataFrame(y).to_json(orient='records') for x, y in c.sort_values(by='date').groupby('state', as_index=False)]

statesJson = ", ".join(states);
statesJson = "[" + statesJson + "]"

script = "window.displayChart(`{}`, element, {{ chartTitle: 'covid deaths by state', excludedProperties: ['*cases', '*fips'], extractTitle: 'state' }})".format(statesJson)

Javascript(script)

<IPython.core.display.Javascript object>

Next we display the cases by state. 

In [5]:
import json
from IPython.display import Javascript

script = "window.displayChart(`{}`, element, {{ chartTitle: 'covid cases by state', excludedProperties: ['*deaths', '*fips'], extractTitle: 'state'  }})".format(statesJson)

Javascript(script)

<IPython.core.display.Javascript object>

Next we display the raw data in a grid.

In [6]:
import json
from IPython.display import Javascript

script = "window.displayGrid(`{}`, element, {{ defaultColumnMinWidth: 100, dataSourceDesiredProperties: ['date', 'state', 'cases', 'deaths'] }})".format(statesJson)

Javascript(script)

<IPython.core.display.Javascript object>